In [7]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [8]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [9]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/FinancialProgressReport/finProgress_newRpt.aspx"
params = {
    'params': 0
}
for key, value in params.items():
    url = url #+ "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [10]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddl_finYear'
iay_radio_name = 'ctl00$ContentPlaceHolder1$rdlScheme'
excel_button = 'ctl00$ContentPlaceHolder1$btnExport'
content_table_class = 'table_s'

In [11]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

def check_table():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.CSS_SELECTOR, '.'+content_table_class))            
    WebDriverWait(driver, 2).until(element_present)
    
#Check Submit button
def delete_excel():
    driver.execute_script("return document.getElementsByName('" + excel_button + "')[0].remove()")
def check_excel():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, excel_button ) ) )

In [12]:
#Start Chrome
driver.get(url)
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[2:3]
print(yearlist)
for year in yearlist:
    print("--Scrapping data for Year: ", year['text'])
    #Start Chrome
    driver.get(url)
    #Year Selection
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(".//option[@value='0']").click()
    year_query = ".//option[@value='" + year['value'] + "']"
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    
    #DataStore
    df_list = []
    
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, iay_radio_name))
    )
    element.click()
    
    #state select
    check_table()
    temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[3:-2]
    states = []
    for row in temp_list:
        try:
            x = {}
            td = row.find_elements_by_xpath(".//td")[1]
            x['name'] = td.text
            x['link'] = td.find_element_by_tag_name("a").get_attribute("href")
            states.append(x)
        except Exception as e:
            print("Error while parsing table data |", e)
    for state in states:
        print("----Scrapping data for State: ", state['name'])
        driver.get(state['link'])
        check_table()
        temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
        districts = []
        for row in temp_list:
            x = {}            
            x['name'] = row.find_elements_by_xpath(".//td")[1].text
            x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
            districts.append(x)
        for district in districts:
            print("------Scrapping data for District: ", district['name'])
            driver.get(district['link'])
            check_table()
            temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
            blocks = []
            for row in temp_list:
                x = {}            
                x['name'] = row.find_elements_by_xpath(".//td")[1].text
                x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
                blocks.append(x)
            
            for block in blocks:
                print("--------Scrapping data for Block: ", block['name'])
                driver.get(block['link'])
                check_table()
                html_table = driver.find_element_by_class_name(content_table_class).get_attribute('outerHTML')
                df = pd.read_html(html_table, header=3)[0]
                df = df[:-1]
                #df.columns = table_head
                df['Financial Year'] = year['text']
                df['State Name'] = state['name']
                df['District Name'] = district['name']
                df['Block Name'] = block['name']
                df_list.append(df)
                #except Exception as e:
                #    print("Error while table data |", e)
                
    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df.drop(df.columns[0],axis=1,inplace=True)
    df = df.reset_index()
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

[{'text': '2012-2013', 'value': '2012-2013 '}]
--Scrapping data for Year:  2012-2013
Error while parsing table data | Message: no such element: Unable to locate element: {"method":"tag name","selector":"a"}
  (Session info: chrome=66.0.3359.181)
  (Driver info: chromedriver=2.35.528161 (5b82f2d2aae0ca24b877009200ced9065a772e73),platform=Windows NT 10.0.17134 x86_64)

----Scrapping data for State:  ARUNACHAL PRADESH
----Scrapping data for State:  ASSAM
------Scrapping data for District:  BAKSA
--------Scrapping data for Block:  Barama
--------Scrapping data for Block:  Baska
--------Scrapping data for Block:  Dhamdhama
--------Scrapping data for Block:  Goreswar
--------Scrapping data for Block:  Jalah(BTC)
--------Scrapping data for Block:  Nagrijuli
--------Scrapping data for Block:  Tamulpur
------Scrapping data for District:  BARPETA
--------Scrapping data for Block:  BAJALI
--------Scrapping data for Block:  BARPETA
--------Scrapping data for Block:  BHAWANIPUR
--------Scrapping da

--------Scrapping data for Block:  MAYONG
--------Scrapping data for Block:  MOIRABARI
------Scrapping data for District:  NAGAON
--------Scrapping data for Block:  Bajiagaon
--------Scrapping data for Block:  Barhampur
--------Scrapping data for Block:  Batadraba
--------Scrapping data for Block:  Binakandi
--------Scrapping data for Block:  Dhalpukhuri
--------Scrapping data for Block:  Dolongghat
--------Scrapping data for Block:  Jugijan
--------Scrapping data for Block:  Juria
--------Scrapping data for Block:  Kaliabor
--------Scrapping data for Block:  Kathiatoli
--------Scrapping data for Block:  Khagorijan
--------Scrapping data for Block:  Lowkhowa
--------Scrapping data for Block:  Lumding
--------Scrapping data for Block:  Odali
--------Scrapping data for Block:  Pachim Kaliabor
--------Scrapping data for Block:  Pakhimoria
--------Scrapping data for Block:  Raha
--------Scrapping data for Block:  Rupahihut
------Scrapping data for District:  NALBARI
--------Scrapping data 

--------Scrapping data for Block:  BIRAUL
--------Scrapping data for Block:  DARBHANGA
--------Scrapping data for Block:  GAURABAURAM
--------Scrapping data for Block:  GHANSHYAMPUR
--------Scrapping data for Block:  HANUMAN NAGAR
--------Scrapping data for Block:  HAYAGHAT
--------Scrapping data for Block:  JALE
--------Scrapping data for Block:  KEOTIRUNWAY
--------Scrapping data for Block:  KIRATPUR
--------Scrapping data for Block:  KUSHESHWAR ASTHAN
--------Scrapping data for Block:  KUSHESWAR ASTHAN EAST
--------Scrapping data for Block:  MANIGACHHI
--------Scrapping data for Block:  SINGHWARA
--------Scrapping data for Block:  TARDIH
------Scrapping data for District:  GAYA
--------Scrapping data for Block:  AMAS
--------Scrapping data for Block:  ATRI
--------Scrapping data for Block:  BANKEY BAZAR
--------Scrapping data for Block:  BARACHATTI
--------Scrapping data for Block:  BATHANI
--------Scrapping data for Block:  BELAGANJ
--------Scrapping data for Block:  BODHGAYA
-----

--------Scrapping data for Block:  SAHEBGANJ
--------Scrapping data for Block:  Sakra
--------Scrapping data for Block:  SARAIYA
------Scrapping data for District:  NALANDA
--------Scrapping data for Block:  ASTHAWAN BLOCK
--------Scrapping data for Block:  BEN
--------Scrapping data for Block:  BIHARSARIF
--------Scrapping data for Block:  BIND BLOCK
--------Scrapping data for Block:  CHANDI BLOCK
--------Scrapping data for Block:  EKANGARSARAI
--------Scrapping data for Block:  GIRIYAK
--------Scrapping data for Block:  HARNAUT BLOCK
--------Scrapping data for Block:  HILSA
--------Scrapping data for Block:  ISLAMPUR BLOCK
--------Scrapping data for Block:  KARAIPARSURAI
--------Scrapping data for Block:  KATRISARAI
--------Scrapping data for Block:  NAGARNAUSA
--------Scrapping data for Block:  NOORSARAI
--------Scrapping data for Block:  PARWALPUR
--------Scrapping data for Block:  RAHUI BLOCK
--------Scrapping data for Block:  RAJGIR BLOCK
--------Scrapping data for Block:  SARMER

--------Scrapping data for Block:  EKMA
--------Scrapping data for Block:  GARKHA
--------Scrapping data for Block:  ISUAPUR
--------Scrapping data for Block:  JALALPUR
--------Scrapping data for Block:  LAHLADPUR
--------Scrapping data for Block:  MAKER
--------Scrapping data for Block:  MANJHI
--------Scrapping data for Block:  MARHAURA
--------Scrapping data for Block:  MASHRAKH
--------Scrapping data for Block:  NAGRA
--------Scrapping data for Block:  PANAPUR
--------Scrapping data for Block:  PARSA
--------Scrapping data for Block:  REVELGANJ
--------Scrapping data for Block:  SONEPUR
--------Scrapping data for Block:  TARAIYA
------Scrapping data for District:  Sheikhpura
--------Scrapping data for Block:  ARIARI
--------Scrapping data for Block:  BARBHIGA
--------Scrapping data for Block:  CHEWARA
--------Scrapping data for Block:  GHAT KHUSUMBAHA
--------Scrapping data for Block:  SHEIKHPURA
--------Scrapping data for Block:  SHEOKHOPUR SARAI
------Scrapping data for District:

...

--------Scrapping data for Block:  NAWABGANJ
--------Scrapping data for Block:  RAJEPUR
--------Scrapping data for Block:  SHAMSABAD
------Scrapping data for District:  FATEHPUR
--------Scrapping data for Block:  AIRAYA
--------Scrapping data for Block:  AMAULI
--------Scrapping data for Block:  ASODHAR
--------Scrapping data for Block:  BAHUA
--------Scrapping data for Block:  BHITAURA
--------Scrapping data for Block:  DEVMAI
--------Scrapping data for Block:  DHATA
--------Scrapping data for Block:  HASWA
--------Scrapping data for Block:  HATHGAON
--------Scrapping data for Block:  KHAJUHA
--------Scrapping data for Block:  MALWAN
--------Scrapping data for Block:  TELYANI
--------Scrapping data for Block:  VIJAYIPUR
------Scrapping data for District:  GAUTAM BUDDHA NAGAR
--------Scrapping data for Block:  Bisrakh
--------Scrapping data for Block:  Dadri
--------Scrapping data for Block:  Dankaur
--------Scrapping data for Block:  Jewar
------Scrapping data for District:  GHAZIPUR


--------Scrapping data for Block:  SIDHPURA
--------Scrapping data for Block:  SORON
------Scrapping data for District:  KAUSHAMBI
--------Scrapping data for Block:  chail
--------Scrapping data for Block:  kara
--------Scrapping data for Block:  kaushambi
--------Scrapping data for Block:  manjhanpur
--------Scrapping data for Block:  mooratganj
--------Scrapping data for Block:  Nevada
--------Scrapping data for Block:  sarsawan
--------Scrapping data for Block:  sirathu
------Scrapping data for District:  KHERI
--------Scrapping data for Block:  BANKEYGANJ
--------Scrapping data for Block:  BEHJAM
--------Scrapping data for Block:  BIJUA
--------Scrapping data for Block:  DHAUREHRA
--------Scrapping data for Block:  ISANAGAR
--------Scrapping data for Block:  KUMBHIGOLA
--------Scrapping data for Block:  LAKHIMPUR
--------Scrapping data for Block:  MITAULI
--------Scrapping data for Block:  MOHAMMADI
--------Scrapping data for Block:  NAKAHA
--------Scrapping data for Block:  NIGHAS

--------Scrapping data for Block:  SARSAWAN
------Scrapping data for District:  SAMBHAL
--------Scrapping data for Block:  ASMAULI
--------Scrapping data for Block:  BAHJOI
--------Scrapping data for Block:  BANIYAKHERA
--------Scrapping data for Block:  GUNNAUR
--------Scrapping data for Block:  PANWASA
--------Scrapping data for Block:  SAMBHAL
------Scrapping data for District:  SANT KABEER NAGAR
--------Scrapping data for Block:  BAGHAULI
--------Scrapping data for Block:  BELHAR KALA
--------Scrapping data for Block:  HAISAR BAZAR
--------Scrapping data for Block:  KHALILABAD
--------Scrapping data for Block:  MEHDAWAL
--------Scrapping data for Block:  NATH NAGAR
--------Scrapping data for Block:  PAULI
--------Scrapping data for Block:  SANTHA
--------Scrapping data for Block:  SEMARIYAWAN
------Scrapping data for District:  SANT RAVIDAS NAGAR
--------Scrapping data for Block:  ABHOLI
--------Scrapping data for Block:  Gyanpur
--------Scrapping data for Block:  Suriyavan
------S

------Scrapping data for District:  PAURI GARHWAL
--------Scrapping data for Block:  Bironkhal
--------Scrapping data for Block:  Duggada
--------Scrapping data for Block:  Dwarikhal
--------Scrapping data for Block:  Ekeshwar
--------Scrapping data for Block:  Kaljikhal
--------Scrapping data for Block:  Khirsu
--------Scrapping data for Block:  Kot
--------Scrapping data for Block:  Nainidanda
--------Scrapping data for Block:  Pabau
--------Scrapping data for Block:  Pauri
--------Scrapping data for Block:  Pokhra
--------Scrapping data for Block:  Rikhnikhal
--------Scrapping data for Block:  THALISAIN
--------Scrapping data for Block:  Yamkeshwar
--------Scrapping data for Block:  ZAHRIKHAL
------Scrapping data for District:  PITHORAGARH
--------Scrapping data for Block:  Berinag
--------Scrapping data for Block:  Dharchula
--------Scrapping data for Block:  Didihat
--------Scrapping data for Block:  GANGOLIHAT
--------Scrapping data for Block:  Kanalichina
--------Scrapping data 

--------Scrapping data for Block:  EGRA-II
--------Scrapping data for Block:  HALDIA
--------Scrapping data for Block:  KHEJURI-I
--------Scrapping data for Block:  KHEJURI-II
--------Scrapping data for Block:  KOLAGHAT
--------Scrapping data for Block:  MAHISHADAL
--------Scrapping data for Block:  MOYNA
--------Scrapping data for Block:  NANDAKUMAR
--------Scrapping data for Block:  NANDIGRAM-I
--------Scrapping data for Block:  NANDIGRAM-II
--------Scrapping data for Block:  PANSKURA-I
--------Scrapping data for Block:  PATASHPUR-I
--------Scrapping data for Block:  PATASHPUR-II
--------Scrapping data for Block:  RAMNAGAR-I
--------Scrapping data for Block:  RAMNAGAR-II
--------Scrapping data for Block:  SHAHID MATANGINI
--------Scrapping data for Block:  SUTAHATA
--------Scrapping data for Block:  TAMLUK
----Scrapping data for State:  ANDAMAN AND NICOBAR
------Scrapping data for District:  NORTH AND MIDDLE ANDAMAN
--------Scrapping data for Block:  DIGLIPUR
--------Scrapping data f